In [62]:
import datetime
import os
import shutil

import tensorflow as tf
from tensorboard.plugins.hparams import api as hp
from tensorflow import keras
from tensorflow.keras import layers
from tensorflow.keras.mixed_precision import experimental as mixed_precision
from tensorflow.keras.metrics import MeanAbsolutePercentageError, MeanAbsoluteError, RootMeanSquaredError

import definitions
from training import train, data
from training.loguniform import LogUniform
from training.stepuniform import StepUniform
from training.steploguniform import StepLogUniform
from scipy.stats.distributions import randint
import numpy as np
import pandas as pd

import altair as alt

#alt.data_transformers.enable('data_server')
alt.data_transformers.disable_max_rows()

policy = mixed_precision.Policy('mixed_float16')
mixed_precision.set_policy(policy)

# Missing Mass Regression
## H -> WW -> lnulnu

In [63]:
dataset = 'H125'
target = 'nu'

In [64]:
jigsaw_train, jigsaw_val, jigsaw_test = data.get_jigsaw(dataset=dataset, target=target)
x_train, y_train, x_val, y_val, x_test, y_test = data.get_datasets(dataset=dataset, target=target, scale_x=True)
print("x_train:")
print(x_train)
print(f"num training samples: {x_train.shape[0]}")
print(f"num validation samples: {x_val.shape[0]}")
print(f"num testing samples: {x_test.shape[0]}")

x_mean = [-0.21931746  0.01414732  0.07634757  0.03271993  0.17313513  0.106
  0.1429699  -0.04686724  0.46652866  0.106     ]
x_std = [2.60189267e+01 2.58930368e+01 2.07010843e+01 2.07878627e+01
 8.37326392e+01 6.80289158e-14 2.07625359e+01 2.06946765e+01
 8.35104710e+01 6.80289158e-14]
x_train:
           METx      METy  Lax_reco  Lay_reco  Laz_reco  Lam_reco  Lbx_reco  \
0     -0.385684 -0.470236  1.491813  0.274558 -1.375876       1.0 -1.004071   
1      1.467444  0.562137 -2.107043 -1.113026 -2.014977       1.0  0.261854   
2      0.801318 -1.543514  0.433313  0.635599 -0.427432       1.0 -1.436216   
3     -0.778773 -0.233567  0.608453 -0.602136  0.962574       1.0  0.369280   
4      1.148450 -1.135467 -1.051204 -0.084590  0.421404       1.0 -0.391107   
...         ...       ...       ...       ...       ...       ...       ...   
79995 -1.331289 -0.571023  0.968558 -0.051121  0.364525       1.0  0.702637   
79996 -1.389753 -0.232370  0.482799 -0.414591  0.180601       1.0  1.2

## Dataset

In [65]:
Nax_gen_chart = alt.Chart(y_test).mark_bar().encode(alt.X(f"{definitions.TARGETS[dataset][target][0]}:Q", bin=alt.Bin(extent=[0, 200], step=5)), y="count()")
Nay_gen_chart = alt.Chart(y_test).mark_bar().encode(alt.X(f"{definitions.TARGETS[dataset][target][1]}:Q", bin=alt.Bin(extent=[0, 200], step=5)), y="count()")
Naz_gen_chart = alt.Chart(y_test).mark_bar().encode(alt.X(f"{definitions.TARGETS[dataset][target][2]}:Q", bin=alt.Bin(extent=[0, 200], step=5)), y="count()")
Nbz_gen_chart = alt.Chart(y_test).mark_bar().encode(alt.X(f"{definitions.TARGETS[dataset][target][3]}:Q", bin=alt.Bin(extent=[0, 200], step=5)), y="count()")
Nax_gen_chart | Nay_gen_chart | Naz_gen_chart | Nbz_gen_chart

alt.HConcatChart(...)

In [66]:
Nax_reco_chart = alt.Chart(jigsaw_test).mark_bar().encode(alt.X(f"{definitions.JIGSAW_TARGETS[dataset][target][0]}:Q", bin=alt.Bin(extent=[0, 200], step=5)), y="count()")
Nay_reco_chart = alt.Chart(jigsaw_test).mark_bar().encode(alt.X(f"{definitions.JIGSAW_TARGETS[dataset][target][1]}:Q", bin=alt.Bin(extent=[0, 200], step=5)), y="count()")
Naz_reco_chart = alt.Chart(jigsaw_test).mark_bar().encode(alt.X(f"{definitions.JIGSAW_TARGETS[dataset][target][2]}:Q", bin=alt.Bin(extent=[0, 200], step=5)), y="count()")
Nbz_reco_chart = alt.Chart(jigsaw_test).mark_bar().encode(alt.X(f"{definitions.JIGSAW_TARGETS[dataset][target][3]}:Q", bin=alt.Bin(extent=[0, 200], step=5)), y="count()")
Nax_reco_chart | Nay_reco_chart | Naz_reco_chart | Nbz_reco_chart

alt.HConcatChart(...)

In [67]:
jigsaw_difference_Nax = pd.DataFrame({'Nax_gen - Nax_reco': y_test.values[:, 0] - jigsaw_test[definitions.JIGSAW_TARGETS[dataset][target][0]].values})
jigsaw_difference_Nax_chart = alt.Chart(jigsaw_difference_Nax).mark_bar().encode(alt.X("Nax_gen - Nax_reco:Q", bin=alt.Bin(extent=[0, 100], step=5)), y="count()")
jigsaw_difference_Nay = pd.DataFrame({'Nay_gen - Nay_reco': y_test.values[:, 1] - jigsaw_test[definitions.JIGSAW_TARGETS[dataset][target][1]].values})
jigsaw_difference_Nay_chart = alt.Chart(jigsaw_difference_Nay).mark_bar().encode(alt.X("Nay_gen - Nay_reco:Q", bin=alt.Bin(extent=[0, 100], step=5)), y="count()")
jigsaw_difference_Naz = pd.DataFrame({'Naz_gen - Naz_reco': y_test.values[:, 2] - jigsaw_test[definitions.JIGSAW_TARGETS[dataset][target][2]].values})
jigsaw_difference_Naz_chart = alt.Chart(jigsaw_difference_Naz).mark_bar().encode(alt.X("Naz_gen - Naz_reco:Q", bin=alt.Bin(extent=[0, 100], step=5)), y="count()")
jigsaw_difference_Nbz = pd.DataFrame({'Nbz_gen - Nbz_reco': y_test.values[:, 3] - jigsaw_test[definitions.JIGSAW_TARGETS[dataset][target][3]].values})
jigsaw_difference_Nbz_chart = alt.Chart(jigsaw_difference_Nbz).mark_bar().encode(alt.X("Nbz_gen - Nbz_reco:Q", bin=alt.Bin(extent=[0, 100], step=5)), y="count()")
jigsaw_difference_Nax_chart | jigsaw_difference_Nay_chart | jigsaw_difference_Naz_chart | jigsaw_difference_Nbz_chart

alt.HConcatChart(...)

## Results

In [68]:
df_train, df_val, df_test = data.get_datasets(dataset=dataset, target=target, x_y_split=False)

print(df_train)

Hx_gen  Hy_gen     Hz_gen  Hm_gen       Hx_reco       Hy_reco  \
0        -0.0     0.0 -462.33320   125.0  0.000000e+00  4.440892e-15   
1         0.0     0.0 -540.76140   125.0 -1.421085e-14  0.000000e+00   
2         0.0     0.0 -302.00290   125.0  0.000000e+00 -8.881784e-15   
3         0.0    -0.0  339.42230   125.0  8.881784e-15 -1.065814e-14   
4        -0.0     0.0  244.77860   125.0  1.776357e-14  4.440892e-16   
...       ...     ...        ...     ...           ...           ...   
79995     0.0     0.0  167.81920   125.0 -3.552714e-15 -1.776357e-15   
79996    -0.0    -0.0  -34.02435   125.0 -1.776357e-15  3.552714e-15   
79997    -0.0    -0.0  767.80310   125.0  0.000000e+00  0.000000e+00   
79998    -0.0    -0.0  -98.31551   125.0 -3.552714e-15  0.000000e+00   
79999     0.0     0.0  837.30960   125.0  0.000000e+00  3.552714e-15   

         Hz_reco    Hm_reco    Wax_gen    Way_gen  ...    Nbx_gen    Nby_gen  \
0     -263.27580  128.90760  33.930650  10.610390  ... -13.226

In [69]:
log_dir = definitions.LOG_DIR / dataset / 'fix-nu-v2'
model = tf.keras.models.load_model(str(log_dir / 'best_model.h5'))

In [70]:
y_pred = model.predict(x_test)
mean = np.mean(y_train).values
std = np.std(y_train).values
y_pred = y_pred * std + mean
print(y_pred)

[[-0.63588686  2.24632091 -6.08346457  5.04408701]
 [-0.63588686  2.24632091 -6.08346457  5.04408701]
 [-0.63588686  2.24632091 -6.08346457  5.04408701]
 ...
 [-0.63588686  2.24632091 -6.08346457  5.04408701]
 [-0.63588686  2.24632091 -6.08346457  5.04408701]
 [-0.63588686  2.24632091 -6.08346457  5.04408701]]


In [71]:
print(jigsaw_test)
print(y_test)
print(y_pred)

Nax_reco   Nay_reco   Naz_reco    Nbz_reco
0      6.133221  33.823960   12.93972   29.560450
1    -18.267890 -21.116640  -31.31883 -140.937800
2     10.463300 -44.193660  157.14770  165.316700
3     33.694610 -11.768850   69.92698   47.082390
4    -11.203410  25.987010  -80.83449  -28.112800
...         ...        ...        ...         ...
9995 -20.101950  11.728790   59.51912   84.950160
9996  14.759800  -2.551917  -39.53232 -118.479000
9997  -4.632653 -14.447920    6.00164    6.374954
9998 -18.708870  -8.249379   28.43143  151.108200
9999  19.258010  -2.164513 -122.73540 -217.848500

[10000 rows x 4 columns]
        Nax_gen    Nay_gen     Naz_gen     Nbz_gen
0      2.314114  12.492300  -19.552300   -9.673151
1     -4.793596  -5.698381  -69.268640  -38.978670
2     -4.498787   6.614501    8.131576   32.906390
3      1.986047  17.524520   51.868040   16.743930
4     -8.463210  -7.345803  -52.134420 -200.526000
...         ...        ...         ...         ...
9995   4.677482  -3.0738

In [72]:
jigsaw_test = jigsaw_test.values
y_test = y_test.values
print(jigsaw_test)
print(y_test)

[[   6.133221   33.82396    12.93972    29.56045 ]
 [ -18.26789   -21.11664   -31.31883  -140.9378  ]
 [  10.4633    -44.19366   157.1477    165.3167  ]
 ...
 [  -4.632653  -14.44792     6.00164     6.374954]
 [ -18.70887    -8.249379   28.43143   151.1082  ]
 [  19.25801    -2.164513 -122.7354   -217.8485  ]]
[[   2.314114   12.4923    -19.5523     -9.673151]
 [  -4.793596   -5.698381  -69.26864   -38.97867 ]
 [  -4.498787    6.614501    8.131576   32.90639 ]
 ...
 [  11.82702    21.70403   -51.05338     3.21093 ]
 [  34.44451   -15.19392    54.71562    58.40485 ]
 [ -13.42579   -26.4406   -186.8114    -97.59522 ]]


In [73]:
def make_chart_data(idx):
    return pd.DataFrame({'Jigsaw': jigsaw_test[:, idx] - y_test[:, idx], 'NN': y_pred[:, idx] - y_test[:, idx]})
Nax_chart_data = make_chart_data(0)
Nay_chart_data = make_chart_data(1)
Naz_chart_data = make_chart_data(2)
Nbz_chart_data = make_chart_data(3)

In [74]:
def make_chart(chart_data, name):
    return alt.Chart(chart_data).transform_fold(['Jigsaw', 'NN'], as_=['Method', name]).mark_area(interpolate='step-after', line=True, opacity=0.7).encode(alt.X(f"{name}:Q", bin=alt.Bin(extent=[-100, 100], step=5)), y=alt.Y("count()", stack=None), color='Method:N')
Nax_chart = make_chart(Nax_chart_data, 'Nax error')
Nay_chart = make_chart(Nay_chart_data, 'Nay error')
Naz_chart = make_chart(Naz_chart_data, 'Naz error')
Nbz_chart = make_chart(Nbz_chart_data, 'Nbz error')
Nax_chart | Nay_chart | Naz_chart | Nbz_chart

alt.HConcatChart(...)

In [75]:
print('Jigsaw:')
print('\tmae = ' + str(tf.keras.losses.MAE(np.transpose(y_test), np.transpose(jigsaw_test)).numpy()))
print(f'\tmape = ' + str(tf.keras.losses.MAPE(np.transpose(y_test), np.transpose(jigsaw_test)).numpy()))
print('\trmse = ' + str(tf.keras.losses.MSE(np.transpose(y_test), np.transpose(jigsaw_test)).numpy()**0.5))
print('NN:')
print('\tmae = ' + str(tf.keras.losses.MAE(np.transpose(y_test), np.transpose(y_pred)).numpy()))
print('\tmape = ' + str(tf.keras.losses.MAPE(np.transpose(y_test), np.transpose(y_pred)).numpy()))
print('\trmse = ' + str(tf.keras.losses.MSE(np.transpose(y_test), np.transpose(y_pred)).numpy()**0.5))

Jigsaw:
	mae = [22.01058452 22.0039148  98.14378848 99.78789455]
	mape = [918.00857536 705.03469392 800.91343503 961.40603564]
	rmse = [ 26.00207054  25.95102474 169.48412558 176.76883517]
NN:
	mae = [ 15.10238116  15.51342322 111.78419356 114.22490782]
	mape = [123.78498392 152.26118731 180.30527418 171.15372577]
	rmse = [ 19.28002417  19.60855108 193.52747144 200.96227029]


In [76]:
df_test['Nam_pred'] = 0.0
df_test['Nbm_pred'] = 0.0
df_test['Nax_pred'] = y_pred[:, 0]
df_test['Nay_pred'] = y_pred[:, 1]
df_test['Naz_pred'] = y_pred[:, 2]
df_test['Nbz_pred'] = y_pred[:, 3]
data.calc_H125(df_test)

In [77]:
def make_chart_data(name):
    return pd.DataFrame({'Jigsaw': df_test[f'{name}_reco'] - df_test[f'{name}_gen'], 'NN': df_test[f'{name}_pred'] - df_test[f'{name}_gen']})
Nbx_chart_data = make_chart_data('Nbx')
Nby_chart_data = make_chart_data('Nby')

In [78]:
def make_chart(chart_data, name):
    return alt.Chart(chart_data).transform_fold(['Jigsaw', 'NN'], as_=['Method', name]).mark_area(interpolate='step-after', line=True, opacity=0.7).encode(alt.X(f"{name}:Q", bin=alt.Bin(extent=[-100, 100], step=5)), y=alt.Y("count()", stack=None), color='Method:N')
Nbx_chart = make_chart(Nbx_chart_data, 'Nbx error')
Nby_chart = make_chart(Nby_chart_data, 'Nby error')
Nbx_chart | Nby_chart

alt.HConcatChart(...)

In [80]:
Wam_chart_data = pd.DataFrame({'Generator': df_test['Wam_gen'], 'Jigsaw': df_test['Wam_reco'], 'NN': df_test['Wam_pred']})
Wam_chart = alt.Chart(Wam_chart_data).transform_fold(['Generator', 'Jigsaw', 'NN'], as_=['Method', 'Wam']).mark_area(interpolate='step-after', line=True, opacity=0.7).encode(alt.X("Wam:Q", bin=alt.Bin(extent=[38, 102], step=1)), y=alt.Y("count()", stack=None, scale=alt.Scale(type='log')), color='Method:N')
Wbm_chart_data = pd.DataFrame({'Generator': df_test['Wbm_gen'], 'Jigsaw': df_test['Wbm_reco'], 'NN': df_test['Wbm_pred']})
Wbm_chart = alt.Chart(Wbm_chart_data).transform_fold(['Generator', 'Jigsaw', 'NN'], as_=['Method', 'Wbm']).mark_area(interpolate='step-after', line=True, opacity=0.7).encode(alt.X("Wbm:Q", bin=alt.Bin(extent=[38, 102], step=1)), y=alt.Y("count()", stack=None, scale=alt.Scale(type='log')), color='Method:N')
Wam_chart | Wbm_chart

alt.HConcatChart(...)

In [81]:
Hm_chart_data = pd.DataFrame({'Jigsaw': df_test['Hm_reco'], 'NN': df_test['Hm_pred']})
Hm_chart = alt.Chart(Hm_chart_data).transform_fold(['Jigsaw', 'NN'], as_=['Method', 'Hm']).mark_area(interpolate='step-after', line=True, opacity=0.7).encode(alt.X("Hm:Q", bin=alt.Bin(extent=[0, 325], step=4)), y=alt.Y("count()", stack=None), color='Method:N')
Hm_chart

alt.Chart(...)